In [3]:
!pip install miditoolkit
!pip install numpy
# !pip install utils

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 51 kB 1.7 MB/s 
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import miditoolkit
import numpy as np
import os
import utils # file

ModuleNotFoundError: ignored

**Match LPD-5-Cleansed with LMD-matched**

In [ ]:
# dataset link: https://salu133445.github.io/lakh-pianoroll-dataset/dataset 

In [ ]:
# untar lmd_matched.tar.gz to local
!tar -xzvf "/content/drive/MyDrive/Capstone/dataset/lmd_matched.tar.gz" -C "./"

In [ ]:
# untar lpd_5_matched.tar.gz to local
# lpd_5_matched: 1 track multiple recordings
# lpd_5_cleansed: 1 track 1 recording
!tar -xzvf "/content/drive/MyDrive/Capstone/dataset/lpd_5_matched.tar.gz" -C "./"

In [ ]:
# d9014ef7a971eacc57c5e8a06bb4c38f

In [ ]:
# get file list
with open("/content/drive/MyDrive/Capstone/dataset/matched_msdID", "r") as f:
  filelist = f.readlines()

In [ ]:
# filelist
FILES = []
for i in filelist:
  filename = i.rstrip('\n')
  # loc_lpd = "lpd_5/lpd_5_matched/"
  loc_lmd = "lmd_matched/"
  loc = "{}/{}/{}/{}/".format(filename[2], filename[3], filename[4], filename)
  for i in os.listdir(loc_lmd + loc):
    if i.rstrip('.mid') == "d9014ef7a971eacc57c5e8a06bb4c38f":
      print(filename)
      print(loc)
      break

TRRBDXC128F9312D09
R/B/D/TRRBDXC128F9312D09/


In [ ]:
FILES = []
for i in filelist:
  filename = i.rstrip('\n')
  loc_lpd = "lpd_5/lpd_5_matched/"
  loc_lmd = "lmd_matched/"
  loc = "{}/{}/{}/{}/".format(filename[2], filename[3], filename[4], filename)
  for i in os.listdir(loc_lpd + loc):
    FILES.append(loc_lmd + loc + i.rstrip('.npz') + '.mid')
FILES

FileNotFoundError: ignored

In [ ]:
len(FILES)

10913

# Read MIDI (example)

In [ ]:
with np.load("/content/content/results/TRAAAZF12903CCCF6B.npz", allow_pickle=True) as data:
  print(data.items())
print(a)


ItemsView(<numpy.lib.npyio.NpzFile object at 0x7fe87b089790>)
[Event(name=Bar, time=None, value=None, text=1)
 Event(name=Position, time=1920, value=1/16, text=1920)
 Event(name=Chord, time=1920, value=N:N, text=N:N) ...
 Event(name=Note Velocity, time=125760, value=31, text=127/124)
 Event(name=Note On, time=125760, value=66, text=66)
 Event(name=Note Duration, time=125760, value=0, text=64/60)]


In [ ]:
# midi_obj = miditoolkit.midi.parser.MidiFile('/content/1d9d16a9da90c090809c153754823c2b.mid')
midi_obj = miditoolkit.midi.parser.MidiFile('/content/f0e385e9ff35f50379086ce6f32f7afe.mid')

In [ ]:
print(*midi_obj.instruments[0].notes, sep='\n')

In [ ]:
print(*midi_obj.tempo_changes[:10], sep='\n')

122.00081333875559 BPM at 0 ticks


# Complete process


In [ ]:
import numpy as np
from copy import deepcopy

In [ ]:
# file rename to trackid_recordingid_chunkno
!rm -r results/
!mkdir results/

In [ ]:
# # test
# print(len(FILES))
# for i in FILES[:5]:
#   track_id = i[18:36]
#   recording_id = i[37:-4]
#   fn = f"{track_id}_{recording_id}"
#   # 1
#   note_items, tempo_items = utils.read_items(i)
#   # 2
#   note_items = utils.quantize_items(note_items)
#   # 3 (optional)
#   chord_items = utils.extract_chords(note_items)
#   # 4
#   items = chord_items + tempo_items + note_items
#   max_time = note_items[-1].end
#   groups = utils.group_items(items, max_time)
#   # 5
#   events = utils.item2event(groups)
#   # chunk into 16-bar groups
#   print(len(events))
#   chunks = []
#   new_chunk = []
#   for event in events:
#     # start of new chunk
#     if event.name == 'Bar' and int(event.text) % 16 == 1:
#       if len(new_chunk) != 0:
#         chunks.append(new_chunk)
#       new_event = deepcopy(event)
#       new_event.text = str(int(event.text) % 16)
#       new_chunk = [new_event]
#     # other bar events
#     elif event.name == 'Bar':
#       new_event = deepcopy(event)
#       if int(event.text) % 16 == 0:
#         new_event.text = '16'
#       else:
#         new_event.text = str(int(event.text) % 16)
#       new_chunk.append(new_event)
#     else:
#       new_chunk.append(event)
#   if len(new_chunk) != 0:
#     chunks.append(new_chunk)

#   # countt = 0
#   # for a in chunks:
#   #   for b in a:
#   #     countt += 1
#   #     if b.name == 'Bar':
#   #       print(b.text)
#   # print(countt)
#   # np.savez("/content/example.npz", np.array(events))
#   # print(np.array(events))
#   break

In [ ]:
# complete process of generating remi events
error_list = []
count = 0

for i in FILES:
  track_id = i[18:36]
  recording_id = i[37:-4]

  try:
    # 1
    note_items, tempo_items = utils.read_items(i)
    # 2
    note_items = utils.quantize_items(note_items)
    # 3 (optional)
    chord_items = utils.extract_chords(note_items)
    # 4
    items = chord_items + tempo_items + note_items
    max_time = note_items[-1].end
    groups = utils.group_items(items, max_time)
    # 5
    events = utils.item2event(groups)
    ori_len = len(events)
    # print(np.array(events))

    # break into chunks
    chunks = []
    new_chunk = []
    for event in events:
      # start of new chunk
      if event.name == 'Bar' and int(event.text) % 16 == 1:
        if len(new_chunk) != 0:
          chunks.append(new_chunk)
        new_event = deepcopy(event)
        new_event.text = str(int(event.text) % 16)
        new_chunk = [new_event]
      # other bar events
      elif event.name == 'Bar':
        new_event = deepcopy(event)
        if int(event.text) % 16 == 0:
          new_event.text = '16'
        else:
          new_event.text = str(int(event.text) % 16)
        new_chunk.append(new_event)
      else:
        new_chunk.append(event)
    if len(new_chunk) != 0:
      chunks.append(new_chunk)

    # check len
    new_len = 0
    for chunk in chunks:
      new_len += len(chunk)
    assert ori_len == new_len

    # save files
    for k in range(len(chunks)):
      fn = f"{track_id}_{recording_id}_{k}"
      np.savez("/content/results/{}.npz".format(fn), np.array(chunks[k]))

  except:
    print(count)
    error_list.append(fn)
    print("error:", fn)
  count += 1

128
error: TROUFUC128F145DB88_9d2e89075ffefb302cc619a052d771dc_1
NO CHORD
252
error: TRETDAL128F9307641_a20e8ba0ec4eee3e1c1043c1877d307c_14
NO CHORD
393
error: TRNYUUJ128F1487122_3d058a972c3f06f5d55cf79eb048f675_7
394
error: TRNYUUJ128F1487122_3d058a972c3f06f5d55cf79eb048f675_7
NO CHORD
NO CHORD
664
error: TRBNHPW128F4252572_25a898d48e87d6643bf74151d41e1a19_3
863
error: TRMVKSL128F14640E0_17bdece7e110ec8bf6af3611607f1647_2
866
error: TRMVKSL128F14640E0_d6c0f52ca8ee56baf711a91942d5e969_2
NO CHORD
1122
error: TRQZTFC128F4278EC2_93858f2a245e54f7bc057a40f7ede2a8_1
1175
error: TRTWCPN128E07935CD_06f20555785379ea19106ce4e23d154f_0
NO CHORD
NO CHORD
NO CHORD
NO CHORD
1878
error: TRSMIKE128F4288DD4_cc9abf6d4220e53bfa1f901bef4a98dd_0
1881
error: TRVSPSU12903CAB741_01f7ede891035d5ce5cc6a58c4de612b_3
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
NO CHORD
2881
error: TREVAKA128F92F7A90_be9db0dd5839283

In [ ]:
# !tar -czvf lpd_5_remi_0906.tar.gz /content/results

In [ ]:
len(error_list)

35

In [ ]:
with open('/content/error_list.txt', 'w') as f:
    for track_id in error_list:
        f.write(f"{track_id}\n")
    print('Done')

Done


In [ ]:
# tar file to Gdrive
!tar -czvf "/content/drive/MyDrive/Capstone/dataset/lpd_5_remi_0906.tar.gz" "/content/results"


In [ ]:
f = np.load("example.npz")

In [ ]:
with np.load('example.npz', allow_pickle=True) as data:
    a = data['arr_0']

In [ ]:
a

array([Event(name=Bar, time=None, value=None, text=1),
       Event(name=Position, time=5760, value=1/16, text=5760),
       Event(name=Chord, time=5760, value=N:N, text=N:N), ...,
       Event(name=Note Velocity, time=84360, value=28, text=114/112),
       Event(name=Note On, time=84360, value=33, text=33),
       Event(name=Note Duration, time=84360, value=37, text=2296/2280)],
      dtype=object)

In [ ]:
%cd /content/
%ls

/content
attributes.py                    example.npz             results/
chord_recognition.py             lmd_matched/            sample_data/
compound-word-transformer-main/  lpd_5/                  utils.py
drive/                           lpd_5_remi_0906.tar.gz
error_list.txt                   __pycache__/


**Finished processing data into REMI events**

# Process remi events into 4 features

In [ ]:
!unzip "/content/drive/MyDrive/Capstone/dataset/MuseMorphose-main.zip" -d "./"

In [ ]:
# musemorphose example
# download REMI-pop-1.7K dataset
!wget -O remi_dataset.tar.gz https://zenodo.org/record/4782721/files/remi_dataset.tar.gz?download=1
!tar xzvf remi_dataset.tar.gz
!rm remi_dataset.tar.gz

# compute attributes classes
!python3 attributes.py

In [ ]:
!mv remi_dataset remi_dataset_ori

In [ ]:
with open("remi_dataset_ori/9.pkl", "rb") as f:
    testp = pickle.load(f)
len(testp)

2

In [ ]:
# unzip our remi files
!tar xzvf "/content/lpd_5_remi_0906.tar.gz" -C "./"

In [ ]:
# print(os.listdir("/content/content/results/"))

['TRZJOSE128F42380BC_37d1091c4d91fbf4c96a921bd2f1eef0_5.npz', 'TRFEZXA12903CBA501_c6b1a1c86b6ff379ec9d7c9b074959ec_0.npz', 'TRMVKSL128F14640E0_2005849bb6bf87d99e69d606da77ac2f_2.npz', 'TRHQVXA128F92F8201_4e3928c505365a5528e61ca98345503f_1.npz', 'TRCDZAW128F933A974_7146fbbc7625e75754c6d941202870b7_3.npz', 'TRAVSBN128F42A5ADE_0c77baa2417d12f70998f9bb917bb7ff_2.npz', 'TRXRVJE128F931255F_aa5d74ec4b87b364aa1806d52b73c0a6_1.npz', 'TRUMSXH128F4243D0D_16c3c907a62efc94955250497a8e3828_1.npz', 'TRAFISO128E07965C7_23b932508e50b703a605bffda6324c01_4.npz', 'TRYETON128F4223F34_0ec315d7be357f130de5206e67c33b36_0.npz', 'TRXESSH128F4294092_dd2b1b51c94ed6eb80712263131fd4a3_0.npz', 'TRKJHVF128F4273C8E_270f3c999d249ec8d417f84eea57ef44_2.npz', 'TRQFGKR128F9314256_8458d362c85c0718d30da11829a18ba4_0.npz', 'TRHBFEF128F4286196_b5423205aa036b6f21621c1adf8b9175_0.npz', 'TRHVZDT128F427EFBE_5cd4ee7b7490f611a25236e1473c752d_3.npz', 'TRWUUQV128F427A40F_68950550a5956a145b0ccc1510a4836a_2.npz', 'TROTTSQ12903CB4279_120

In [ ]:
def cal_bar_pos(events):
  bar_pos = []
  count = 0
  for event in events:
    if event.name == "Bar":
      bar_pos.append(count)
    count += 1
  return bar_pos

In [ ]:
# add bar_pos and save as pkl files
!rm -r remi_dataset/
!mkdir remi_dataset/
REMI_FOLDER = "/content/content/results/"
for i in os.listdir(REMI_FOLDER):
  fn = i[:-4]
  with np.load(REMI_FOLDER + i, allow_pickle=True) as data:
    event = data['arr_0']
    bar_pos = cal_bar_pos(event)
    if len(bar_pos) > 16:
      print(bar_pos)
  with open(f"/content/remi_dataset/{fn}.pkl", "wb") as f:
    pickle.dump([bar_pos, event], f)

In [ ]:
# with open(f"/content/remi_dataset/{fn}.pkl", "rb") as f:
#     test_ = pickle.load(f)
# test_

In [ ]:
data_dir = 'remi_dataset'
polyph_out_dir = 'remi_dataset/attr_cls/polyph'
rhythm_out_dir = 'remi_dataset/attr_cls/rhythm'

pieces = [p for p in sorted(os.listdir(data_dir)) if '.pkl' in p]
all_r_cls = []
all_p_cls = []

if not os.path.exists(polyph_out_dir):
  os.makedirs(polyph_out_dir)
if not os.path.exists(rhythm_out_dir):
  os.makedirs(rhythm_out_dir)  

# for p in pieces:
#   bar_pos, events = pickle_load(os.path.join(data_dir, p))
#   events = events[ :bar_pos[-1] ]

In [ ]:
import pickle
def pickle_load(f):
  return pickle.load(open(f, 'rb'))

In [ ]:
# copied from attributes.py
import os, pickle
import numpy as np
from collections import Counter

data_dir = 'remi_dataset'
polyph_out_dir = 'remi_dataset/attr_cls/polyph'
rhythm_out_dir = 'remi_dataset/attr_cls/rhythm'

rhym_intensity_bounds = [0.2, 0.25, 0.32, 0.38, 0.44, 0.5, 0.63]
polyphonicity_bounds = [2.63, 3.06, 3.50, 4.00, 4.63, 5.44, 6.44]

def compute_polyphonicity(events, n_bars):
  poly_record = np.zeros( (n_bars * 16,) )

  cur_bar, cur_pos = -1, -1
  for ev in events:
    if ev.name == 'Bar':
      cur_bar += 1
    elif ev.name == 'Beat':
      cur_pos = int(ev.value)
    elif ev.name == 'Note_Duration':
      duration = int(ev.value) // 120
      st = cur_bar * 16 + cur_pos
      poly_record[st:st + duration] += 1
  
  return poly_record

def get_onsets_timing(events, n_bars):
  onset_record = np.zeros( (n_bars * 16,) )

  cur_bar, cur_pos = -1, -1
  # print(events)
  for ev in events:
    if ev.name == 'Bar':
      cur_bar += 1
    elif ev.name == 'Beat':
      cur_pos = int(ev.value)
    elif ev.name == 'Note_Pitch':
      rec_idx = cur_bar * 16 + cur_pos
      onset_record[ rec_idx ] = 1

  return onset_record

In [ ]:
# copied from attributes.py
pieces = [p for p in sorted(os.listdir(data_dir)) if '.pkl' in p]
all_r_cls = []
all_p_cls = []

if not os.path.exists(polyph_out_dir):
  os.makedirs(polyph_out_dir)
if not os.path.exists(rhythm_out_dir):
  os.makedirs(rhythm_out_dir)  


In [ ]:
#copied from attributes.py
count = 0
for p in pieces:
  if count % 500 == 0:
    print(count)
  bar_pos, events = pickle_load(os.path.join(data_dir, p))
  events = events[ :bar_pos[-1] ]
  # print(events)
  for i in events:
    if i.name == "Note Duration":
      print(i)
  if count > 10:
    break
  polyph_raw = np.reshape(
    compute_polyphonicity(events, n_bars=len(bar_pos)), (-1, 16)
  )
  rhythm_raw = np.reshape(
    get_onsets_timing(events, n_bars=len(bar_pos)), (-1, 16)
  )

  polyph_cls = np.searchsorted(polyphonicity_bounds, np.mean(polyph_raw, axis=-1)).tolist()
  rfreq_cls = np.searchsorted(rhym_intensity_bounds, np.mean(rhythm_raw, axis=-1)).tolist()

  pickle.dump(polyph_cls, open(os.path.join(
    polyph_out_dir, p), 'wb'
  ))
  pickle.dump(rfreq_cls, open(os.path.join(
    rhythm_out_dir, p), 'wb'
  ))

  all_r_cls.extend(rfreq_cls)
  all_p_cls.extend(polyph_cls)
  count += 1

print ('[rhythm classes]', Counter(all_r_cls))
print ('[polyph classes]', Counter(all_p_cls))

comments on the previous process:
no "Beat" in events, only "Sub-beat", so cannot calculate those scores. also note duration value is relatively small. (probably will affect score calculation?)

need to check the process handled by https://github.com/YatingMusic/compound-word-transformer/blob/main/dataset/Dataset.md from midi to modified remi to attribute scores.

ends here.

# Starts here

In [ ]:
# mount to drive first

**Remi_dataset used by Musemorphose**

In [ ]:
!pip install chorder
import chorder
import pickle

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 51 kB 7.4 MB/s 


In [ ]:
# !wget -O remi_dataset.tar.gz https://zenodo.org/record/4782721/files/remi_dataset.tar.gz?download=1
# !tar xzvf remi_dataset.tar.gz
# !rm remi_dataset.tar.gz
# !tar xzvf /content/drive/MyDrive/Capstone/dataset/remi_dataset_v2.tar.gz

In [ ]:
!unzip "/content/drive/MyDrive/Capstone/dataset/compound-word-transformer-main.zip" -d "./"

In [ ]:
# untar lmd_matched.tar.gz to local
!tar -xzvf "/content/drive/MyDrive/Capstone/dataset/lmd_matched.tar.gz" -C "./"

In [ ]:
# untar lpd_5_matched.tar.gz to local
# lpd_5_matched: 1 track multiple recordings
# lpd_5_cleansed: 1 track 1 recording
!tar -xzvf "/content/drive/MyDrive/Capstone/dataset/lpd_5_matched.tar.gz" -C "./"

In [ ]:
# get file list
with open("/content/drive/MyDrive/Capstone/dataset/matched_msdID", "r") as f:
  filelist = f.readlines()

In [ ]:
FILES = []
for i in filelist:
  filename = i.rstrip('\n')
  loc_lpd = "lpd_5/lpd_5_matched/"
  loc_lmd = "lmd_matched/"
  loc = "{}/{}/{}/{}/".format(filename[2], filename[3], filename[4], filename)
  for i in os.listdir(loc_lpd + loc):
    FILES.append(loc_lmd + loc + i.rstrip('.npz') + '.mid')
len(FILES)

10913

In [ ]:
filename = [i.split('/')[-1] for i in FILES]
file_track_map = dict(zip(filename, filelist))
print(list(file_track_map.items())[:5])

[('d699a6176ba8a550badc34e0f771bd6b.mid', 'TRIGAFS128F425AD35\n'), ('428c487a54ea907103f0e80eb3359d89.mid', 'TRDOWHT128F14774B6\n'), ('d0eafc1023fda33a88b423009061415d.mid', 'TRLGCEL128F4264494\n'), ('2fde4c7578053123dc1616d9974c2a5a.mid', 'TRJAKOA128E0796023\n'), ('58c0c0cf756648cbe61a4680f3208ee0.mid', 'TRKZOBJ128F428AF61\n')]


In [ ]:
FILES[:5]

['lmd_matched/I/G/A/TRIGAFS128F425AD35/d699a6176ba8a550badc34e0f771bd6b.mid',
 'lmd_matched/D/O/W/TRDOWHT128F14774B6/428c487a54ea907103f0e80eb3359d89.mid',
 'lmd_matched/D/O/W/TRDOWHT128F14774B6/d0eafc1023fda33a88b423009061415d.mid',
 'lmd_matched/L/G/C/TRLGCEL128F4264494/2fde4c7578053123dc1616d9974c2a5a.mid',
 'lmd_matched/L/G/C/TRLGCEL128F4264494/58c0c0cf756648cbe61a4680f3208ee0.mid']

In [ ]:
# copy mid files into "/content/compound-word-transformer-main/dataset/midi_synchronized"
import shutil
for file in FILES:
  shutil.copy(file, "/content/compound-word-transformer-main/dataset/midi_synchronized/"+file.split('/')[-1])

In [ ]:
print(os.listdir("/content/compound-word-transformer-main/dataset/midi_synchronized/"))

['88f61c851913a085faf427816298f70e.mid', '7aff0e2f7c897ac44923720b86559847.mid', '6c3c853947d553826eb4c08411c06c53.mid', 'f2d67ffcacd03851f7bda224bd72a2fa.mid', '6661f3620e71f7358c0bddf3afbac701.mid', '04ee3e3a4138b35621332f5af4013b30.mid', 'b6a36daf91963c8f5b5ecced88dc59b7.mid', '054ac83bf09c97d2df827afc01ee4970.mid', 'a6d25eb14761c2c455df5f1b7a916fe8.mid', 'f847587c79c5d7541164489dada5e58f.mid', 'b662518aa178e3a8d9b4b1864468a356.mid', '824ff055d75935dad2714b5f06748731.mid', 'ea31849db57dea83d674539fa5b73fbb.mid', 'cd02c02e9cc7b955759793e1eda92d81.mid', '256a9fc2b01c759bb86f3a700820283f.mid', '7830e74ad025ddd95017bfd69878f371.mid', '3b11b1ec0d8cbcfc9796af234c447bfe.mid', '3e324de36b77e3e3df0fbcacce30aafa.mid', 'e214f5663d3f2d432341ccc9710ca2f6.mid', '77ddb0284a6c16be91a85a1480ae5cc0.mid', '4f5a09460f1512f9f884d43c48233e6b.mid', '726c189b6fb164fbd15e786e13a5127a.mid', 'c5f323fc93cb018b61d5e90b3045e39c.mid', '9a9067eaee7ab5b56d15540fdc43d784.mid', 'b2024f16571416a63c18a8657a5c62a5.mid',

In [ ]:
%cd /content/compound-word-transformer-main/dataset/

/content/compound-word-transformer-main/dataset


In [ ]:
# melody extraction, chord recognition 
# midi_synchronized to midi_analyzed
# takes about 3hrs
!python3 analyzer.py

Streaming output truncated to the last 5000 lines.
 > ./midi_synchronized/d32dc770f78fb92418f9cc0717616e50.mid
 > ./midi_analyzed/d32dc770f78fb92418f9cc0717616e50.mid
 > [global] bpm: 62
----
 > ./midi_synchronized/d32f03c08f033be80cf2e0aab4cf1536.mid
 > ./midi_analyzed/d32f03c08f033be80cf2e0aab4cf1536.mid
 > [global] bpm: 81
 > [global] bpm: 71
----
 > ./midi_synchronized/d339262210df4f35e5643dd676d84353.mid
 > ./midi_analyzed/d339262210df4f35e5643dd676d84353.mid
----
 > ./midi_synchronized/ef3a59fdd81f9a8b059de5651047f7c1.mid
 > ./midi_analyzed/ef3a59fdd81f9a8b059de5651047f7c1.mid
 > [global] bpm: 120
----
 > ./midi_synchronized/ef3c2787b3a9466751c009354b8de10a.mid
 > ./midi_analyzed/ef3c2787b3a9466751c009354b8de10a.mid
 > [global] bpm: 100
 > [global] bpm: 112
----
 > ./midi_synchronized/d344d1187c6852ad5eb98f10c4371d32.mid
 > ./midi_analyzed/d344d1187c6852ad5eb98f10c4371d32.mid
----
 > ./midi_synchronized/ef41133867041cd16945edc7cda75077.mid
 > ./midi_analyzed/ef41133867041cd16945e

In [ ]:
# tar intermediate results to Gdrive
!tar -czvf "/content/drive/MyDrive/Capstone/dataset/compound-word-transformer-main-analyzed.tar.gz" "/content/compound-word-transformer-main"

In [ ]:
# # untar intermediate results to local
# !tar -xzvf "/content/drive/MyDrive/Capstone/dataset/compound-word-transformer-main-analyzed.tar.gz" -C "./"

In [ ]:
# quantization, to corpus
!python3 midi2corpus.py

Streaming output truncated to the last 5000 lines.
 > offset: 0
 > last_bar: 30
7743/9409
 > offset: 0
 > last_bar: 18
7744/9409
 > offset: 6
 > last_bar: 90
7745/9409
 > offset: 0
 > last_bar: 46
7746/9409
 > offset: 0
 > last_bar: 27
7747/9409
 > offset: 0
 > last_bar: 76
7748/9409
 > offset: 8
 > last_bar: 77
7749/9409
 > offset: 1
 > last_bar: 58
7750/9409
 > offset: 0
 > last_bar: 12
7751/9409
 > offset: 0
 > last_bar: 32
7752/9409
 > offset: 2
 > last_bar: 148
7753/9409
 > offset: 0
 > last_bar: 30
7754/9409
 > offset: 1
 > last_bar: 107
7755/9409
 > offset: 0
 > last_bar: 21
7756/9409
 > offset: 10
 > last_bar: 74
7757/9409
 > offset: 1
 > last_bar: 80
7758/9409
 > offset: 0
 > last_bar: 13
7759/9409
 > offset: 0
 > last_bar: 15
7760/9409
 > offset: 2
 > last_bar: 142
7761/9409
 > offset: 1
 > last_bar: 184
7762/9409
 > offset: 1
 > last_bar: 113
7763/9409
 > offset: 0
 > last_bar: 11
7764/9409
 > offset: 42
 > last_bar: 119
7765/9409
 > offset: 0
 > last_bar: 16
7766/9409
 > of

In [ ]:
# tar intermediate results to Gdrive
!tar -czvf "/content/drive/MyDrive/Capstone/dataset/compound-word-transformer-main-corpus.tar.gz" "/content/compound-word-transformer-main"

In [ ]:
# # untar intermediate results to local
# !tar -xzvf "/content/drive/MyDrive/Capstone/dataset/compound-word-transformer-main-corpus.tar.gz" -C "./"

In [ ]:
%cd /content/compound-word-transformer-main/dataset/representations/uncond/remi/
%ls
!python3 corpus2events.py

Streaming output truncated to the last 5000 lines.
 > num_token: 6234
6911/9409
 > num_token: 1342
6912/9409
 > num_token: 1621
6913/9409
 > num_token: 4240
6914/9409
 > num_token: 8318
6915/9409
 > num_token: 2004
6916/9409
 > num_token: 1594
6917/9409
 > num_token: 1269
6918/9409
 > num_token: 2953
6919/9409
 > num_token: 1746
6920/9409
 > num_token: 11283
6921/9409
 > num_token: 939
6922/9409
 > num_token: 1021
6923/9409
 > num_token: 741
6924/9409
 > num_token: 2693
6925/9409
 > num_token: 1947
6926/9409
 > num_token: 1898
6927/9409
 > num_token: 183
6928/9409
 > num_token: 2851
6929/9409
 > num_token: 6151
6930/9409
 > num_token: 7592
6931/9409
 > num_token: 1760
6932/9409
 > num_token: 1328
6933/9409
 > num_token: 7760
6934/9409
 > num_token: 1755
6935/9409
 > num_token: 1677
6936/9409
 > num_token: 3481
6937/9409
 > num_token: 2115
6938/9409
 > num_token: 2
6939/9409
 > num_token: 2256
6940/9409
 > num_token: 9160
6941/9409
 > num_token: 780
6942/9409
 > num_token: 1284
6943/940

In [ ]:
# tar intermediate results to Gdrive
!tar -czvf "/content/drive/MyDrive/Capstone/dataset/compound-word-transformer-main-events.tar.gz" "/content/compound-word-transformer-main"

In [ ]:
# # untar intermediate results to local
# !tar -xzvf "/content/drive/MyDrive/Capstone/dataset/compound-word-transformer-main-events.tar.gz" -C "./"

In [ ]:
!python3 events2words.py

In [ ]:
event_list = os.listdir("/content/compound-word-transformer-main/dataset/representations/uncond/remi/ailab17k_from-scratch_remi/events/")
event_list[:5]

['0b1c847307b711b3a67451c9d2b82ca6.mid.pkl',
 '9c15ab601a1ecb9e386b490a57e18161.mid.pkl',
 '0ae459c95b2ef3ac8682b3211c8a197f.mid.pkl',
 'c4f01f589ccf39d9bb8f6947b0a88a26.mid.pkl',
 '2c158185986fe7482ab094b0d2f08e77.mid.pkl']

In [ ]:
import pickle
EVENT_DIR = "/content/compound-word-transformer-main/dataset/representations/uncond/remi/ailab17k_from-scratch_remi/events/"
event_results = []
for event_file in event_list:
  with open(EVENT_DIR + event_file, "rb") as f:
    tt = pickle.load(f)
  event_results.append(tt)

In [ ]:
# event_results[0]

In [ ]:
# chunk events by bar
event_results_chunk = []
for events in event_results:
  chunks = [] # store chunks for one song (recording), list of lists
  new_chunk = [] # store a single chunk, list
  bar_count = 0
  for event in events:
    # start of new chunk
    if event["name"] == 'Bar' and bar_count < 16:
      new_chunk.append(event)
      bar_count += 1
    elif event["name"] == 'Bar':
      # start of next chunk
      chunks.append(new_chunk)
      bar_count = 1
      new_chunk = [event]
    else:
      # events other than bars
      new_chunk.append(event)
  if len(new_chunk) != 0:
    chunks.append(new_chunk)
  event_results_chunk.append(chunks)
assert len(event_results_chunk) == len(event_results)
# assert the number of all events are the same
for i in range(len(event_results)):
  assert len(event_results[i]) == sum([len(c) for c in event_results_chunk[i]])

In [ ]:
# for i in event_results_chunk[4][0]:
#   if i["name"] == "Bar":
#     print(i)

In [ ]:
# generate bar_pos
bar_pos = []
for song in event_results_chunk:
  song_bar_pos = []
  for chunk in song:
    count = 0
    single_f = []
    for ev in chunk:
      if ev["name"] =="Bar":
        # print(count ,i)
        single_f.append(count)
      count += 1
    song_bar_pos.append(single_f)
  bar_pos.append(song_bar_pos)

In [ ]:
for song_bar_pos in bar_pos:
  for chunk_bar_pos in song_bar_pos:
    assert len(chunk_bar_pos) <= 16

In [ ]:
len(bar_pos)

9409

In [ ]:
# recording_chunk_map = list(zip(event_list, event_results_chunk))

In [ ]:
# map chunks to recording id and rename 
chunk_id_list = []
for i in range(len(event_list)):
  track_id = event_list[i].split(".")[0]
  # print(track_id)
  for idx in range(len(event_results_chunk[i])):
    new_id = f"{track_id}_{idx}"
    # print(new_id)
    chunk_id_list.append(new_id)

chunk_id_list[:5]

['0b1c847307b711b3a67451c9d2b82ca6_0',
 '9c15ab601a1ecb9e386b490a57e18161_0',
 '9c15ab601a1ecb9e386b490a57e18161_1',
 '9c15ab601a1ecb9e386b490a57e18161_2',
 '9c15ab601a1ecb9e386b490a57e18161_3']

In [ ]:
# expand event_results_chunk
all_event_chunks = []
for song in event_results_chunk:
    for chunk in song:
        all_event_chunks.append(chunk)

all_bar_pos = []
for song in bar_pos:
    for chunk in song:
        all_bar_pos.append(chunk)

assert len(all_event_chunks) == len(all_bar_pos)
print(len(all_event_chunks))

34241


In [ ]:
all_bar_pos[0]

[0, 280, 552, 764, 1019, 1277, 1611, 1864, 2117, 2397, 2472]

In [ ]:
remi_data = list(zip(all_bar_pos, all_event_chunks))

In [ ]:
# # words = np.load("/content/compound-word-transformer-main/dataset/representations/uncond/remi/ailab17k_from-scratch_remi/words/test.mid.pkl.npy")
# words

array([ 0,  1, 25, ..., 33,  0, 26])

In [ ]:
# !cp /content/midi_analyzed/test.mid /content/compound-word-transformer-main/dataset/midi_analyzed/test.mid

In [ ]:
%cd /content/
# !rm -r remi_dataset
!mkdir remi_dataset

/content
mkdir: cannot create directory ‘remi_dataset’: File exists


In [ ]:
chunk_id_list[0]

'0b1c847307b711b3a67451c9d2b82ca6_0'

In [ ]:
len(remi_data[3][0])

16

In [ ]:
# dir = "/content/drive/MyDrive/Capstone/dataset/lpd-5-remi/"
# generate (bar_pos, remi_events) .pkl files and calculate the attributes later
dir = "/content/remi_dataset/"
for i in range(len(remi_data)):
  with open('{}{}.pkl'.format(dir, chunk_id_list[i]), 'wb') as f:
    pickle.dump(remi_data[i], f)


## Attribute Scores here

In [ ]:
# need to consider the augmented dataset when calculating the boundaries

In [ ]:
# # tar intermediate results to Gdrive
# !tar -czvf "/content/drive/MyDrive/Capstone/dataset/remi_dataset_0907.tar.gz" "/content/remi_dataset"

In [ ]:
# untar intermediate results to local
!tar -xzvf "/content/drive/MyDrive/Capstone/dataset/remi_dataset_0907.tar.gz" -C "./"

In [ ]:
!unzip "/content/drive/MyDrive/Capstone/dataset/MuseMorphose-main.zip" -d "./"

In [ ]:
# !python3 /content/MuseMorphose-main/attributes.py

[rhythm classes] Counter({0: 153656, 7: 115504, 6: 50451, 5: 41513, 2: 32963, 1: 31840, 3: 26032, 4: 21825})
[polyph classes] Counter({0: 424411, 1: 16466, 2: 11606, 3: 10113, 4: 5512, 5: 3749, 6: 1552, 7: 375})


In [4]:
# files that we do not consider because they have no events between some consecutive bars
no_events_d = {}
with open("/content/drive/MyDrive/Capstone/Deep Music Generation Group Folder/dataset/no_events_fn.txt", "r") as f:
  for line in f.readlines():
    fn, num = line.rstrip('\n').split()
    no_events_d[fn] = int(num)
print(no_events_d)

{'a953316683aaba87ed2671b7c5280cad_37.pkl': 15, '00973cf8980c07aa79e7329bb0a2f023_7.pkl': 15, 'a3032c2d567c5ae6b6251451eadcb452_15.pkl': 15, 'a953316683aaba87ed2671b7c5280cad_5.pkl': 15, '82faaf45841fa05f9925b5a59e7013c6_10.pkl': 15, 'a953316683aaba87ed2671b7c5280cad_23.pkl': 15, 'af95c383a443192bb6aa25f2a9832b97_12.pkl': 15, '82faaf45841fa05f9925b5a59e7013c6_11.pkl': 15, 'a953316683aaba87ed2671b7c5280cad_15.pkl': 15, '82faaf45841fa05f9925b5a59e7013c6_13.pkl': 15, '0d51e1ab7360fbc56beb5eaee53a30de_6.pkl': 15, 'a953316683aaba87ed2671b7c5280cad_11.pkl': 15, 'a953316683aaba87ed2671b7c5280cad_45.pkl': 15, 'a953316683aaba87ed2671b7c5280cad_77.pkl': 15, 'a953316683aaba87ed2671b7c5280cad_31.pkl': 15, 'a953316683aaba87ed2671b7c5280cad_9.pkl': 15, '8cfc27ac153e2725803451f916e20142_4.pkl': 15, '28057a33027b2e86ca60c3b56c590287_8.pkl': 15, 'd686c9935a5df1b1e6e77b7be2a1a703_9.pkl': 15, 'a953316683aaba87ed2671b7c5280cad_33.pkl': 15, 'a953316683aaba87ed2671b7c5280cad_7.pkl': 15, '82faaf45841fa05f992

In [5]:
# need to consider augmented dataset
# 8. obtain label files
# located in shared drive /dataset/remi_splitted/
import csv

def print_dict_ex(d):
  print("Printing 3 lines of examples ...")
  count = 0
  for k, v in d.items():
    print(f"{k}: {v}")
    count += 1
    if count >= 3:
      break

def load_tuples(fn):
  fn_map = {}
  recording_track_map = {}
  with open(fn) as csv_file:
    csv_reader = csv.reader(csv_file)
    count = 0
    for row in csv_reader:
      assert len(row) == 2
      if len(row[1])==0:
        print("Dropping out rows with null labels...")
        continue
      if count == 0:
        print(row)
      else:
        track, recording, chunk = row[0].split("_")
        map_id = f"{recording}_{chunk}"
        if f"{map_id}.pkl" in no_events_d:  # remove some files
          continue
        if map_id in fn_map:
          fn_map[map_id].append(row[1])
        else:
          fn_map[map_id] = [row[1]]
      count += 1
    print(f"Processed {count - 1} lines of tuples.")
  return fn_map

neg_test = load_tuples("/content/drive/MyDrive/Capstone/Deep Music Generation Group Folder/dataset/remi_splitted/neg_tuples_test.csv")
neg_train = load_tuples("/content/drive/MyDrive/Capstone/Deep Music Generation Group Folder/dataset/remi_splitted/neg_tuples_train.csv")
neg_val = load_tuples("/content/drive/MyDrive/Capstone/Deep Music Generation Group Folder/dataset/remi_splitted/neg_tuples_val.csv")
pos_test = load_tuples("/content/drive/MyDrive/Capstone/Deep Music Generation Group Folder/dataset/remi_splitted/pos_tuples_test.csv")
pos_train = load_tuples("/content/drive/MyDrive/Capstone/Deep Music Generation Group Folder/dataset/remi_splitted/pos_tuples_train.csv")
pos_val = load_tuples("/content/drive/MyDrive/Capstone/Deep Music Generation Group Folder/dataset/remi_splitted/pos_tuples_val.csv")
print_dict_ex(neg_test)

['file_name', 'label']
Processed 69776 lines of tuples.
['file_name', 'label']
Processed 544785 lines of tuples.
['file_name', 'label']
Processed 54914 lines of tuples.
['file_name', 'label']
Processed 69776 lines of tuples.
['file_name', 'label']
Processed 544785 lines of tuples.
['file_name', 'label']
Processed 54914 lines of tuples.
Printing 3 lines of examples ...
963f64dd7134630efa174e32c9cb8ca1_0: ['Europe,Mambo,Euro Pop,Folk Rock,British Metal,Hungary,Electronic', "Johnny plays great he is a slide guitar master . This show he played each song for 20 minutes making extended jams out of them .The reason i want to only show 3 Stars is because Edgar opened this concert when i saw it in NYC and Jammed with Johnny at the end on Sax .It rained alot that day and there were flood conditions , edgar played Frankinstein for about half an hour . I'm going to check Edgars catalog and see if there are any live jams with Johnny . Edgar is Johnnys equal on Sax.", "Thank you Deicde for making so

In [6]:
len(os.listdir("/content/remi_dataset"))

NameError: ignored

In [7]:
# copied from attributes.py
def pickle_load(f):
  return pickle.load(open(f, 'rb'))

import os, pickle
import numpy as np
from collections import Counter

data_dir = '/content/content/remi_dataset'
polyph_out_dir = '/content/content/remi_dataset/attr_cls/polyph'
rhythm_out_dir = '/content/content/remi_dataset/attr_cls/rhythm'

# rhym_intensity_bounds = [0.2, 0.25, 0.32, 0.38, 0.44, 0.5, 0.63]
# polyphonicity_bounds = [2.63, 3.06, 3.50, 4.00, 4.63, 5.44, 6.44]

def compute_polyphonicity(events, n_bars):
  poly_record = np.zeros( (n_bars * 16,) )

  cur_bar, cur_pos = -1, -1
  for ev in events:
    if ev['name'] == 'Bar':
      cur_bar += 1
    elif ev['name'] == 'Beat':
      cur_pos = int(ev['value'])
    elif ev['name'] == 'Note_Duration':
      duration = int(ev['value']) // 120
      st = cur_bar * 16 + cur_pos
      poly_record[st:st + duration] += 1
  
  return poly_record

def get_onsets_timing(events, n_bars):
  onset_record = np.zeros( (n_bars * 16,) )

  cur_bar, cur_pos = -1, -1
  for ev in events:
    if ev['name'] == 'Bar':
      cur_bar += 1
    elif ev['name'] == 'Beat':
      cur_pos = int(ev['value'])
    elif ev['name'] == 'Note_Pitch':
      rec_idx = cur_bar * 16 + cur_pos
      onset_record[ rec_idx ] = 1

  return onset_record

In [21]:
data_dir

'/content/content/remi_dataset'

In [19]:
# get polyphonicity_bounds & rhym_intensity_bounds

# pieces = [p for p in sorted(os.listdir(data_dir)) if '.pkl' in p]
datasets_to_use = [neg_test, pos_test, neg_val, pos_val, neg_train, pos_train]
pieces = []
for dset in datasets_to_use:
  for k, v in dset.items():
    pieces.extend([k] * len(v))
all_r_raw = []
all_p_raw = []


for idx in range(len(pieces)):
  p = pieces[idx]
  if idx != 0 and p == pieces[idx - 1]: # extend prev result again
    all_p_raw.extend(np.mean(polyph_raw, axis=-1).tolist())
    all_r_raw.extend(np.mean(rhythm_raw, axis=-1).tolist())
    continue
  p = p + '.pkl'
  bar_pos, events = pickle_load(os.path.join(data_dir, p))
  events = events[ :bar_pos[-1] ]

  polyph_raw = np.reshape(
    compute_polyphonicity(events, n_bars=len(bar_pos)), (-1, 16)
  )
  rhythm_raw = np.reshape(
    get_onsets_timing(events, n_bars=len(bar_pos)), (-1, 16)
  )

  all_p_raw.extend(np.mean(polyph_raw, axis=-1).tolist())
  all_r_raw.extend(np.mean(rhythm_raw, axis=-1).tolist())

In [20]:
len(pieces)

1338950

In [21]:
len(all_p_raw)

18463652

In [15]:
len(neg_test["a1042ba95e510fa06e1aee5b66fdebae_0"])

9

In [22]:
all_p_raw.sort()
all_r_raw.sort()

In [26]:
len(all_r_raw)

18463652

In [23]:
for i in range(len(all_r_raw)):
  if all_r_raw[i] == 0.0 and all_r_raw[i+1] != 0.0:
    print(i)
  if all_r_raw[i] != 1.0 and all_r_raw[i+1] == 1.0:
    print(i)

2917245
16275453


In [27]:
(18463652 - 2917245) / 7

2220915.285714286

In [28]:
rhym_intensity_bounds = [0.0]
for i in range(7):
  rhym_intensity_bounds.append(all_r_raw[2220915*(i+1) + 2917245])
rhym_intensity_bounds

[0.0, 0.1875, 0.3125, 0.4375, 0.5625, 0.6875, 0.9375, 1.0]

In [29]:
for i in range(len(all_p_raw)):
  if all_p_raw[i] == 0.0 and all_p_raw[i+1] != 0.0:
    print(i)


5395599


In [30]:
(len(all_p_raw) - 5395599) / 7

1866864.7142857143

In [31]:
polyphonicity_bounds = [0.0]
for i in range(7):
  polyphonicity_bounds.append(all_p_raw[1866864*(i+1) + 5395599])
polyphonicity_bounds[-1] = all_p_raw[-1]
polyphonicity_bounds

[0.0, 0.5, 0.75, 0.9375, 1.25, 2.0, 3.0, 14.0]

In [44]:
# 34241 - 2255

31986

In [32]:
print(rhym_intensity_bounds)
print(polyphonicity_bounds)

[0.0, 0.1875, 0.3125, 0.4375, 0.5625, 0.6875, 0.9375, 1.0]
[0.0, 0.5, 0.75, 0.9375, 1.25, 2.0, 3.0, 14.0]


In [33]:
# copied from attributes.py
# pieces = [p for p in sorted(os.listdir(data_dir)) if '.pkl' in p]
all_r_cls = []
all_p_cls = []

if not os.path.exists(polyph_out_dir):
  os.makedirs(polyph_out_dir)
if not os.path.exists(rhythm_out_dir):
  os.makedirs(rhythm_out_dir)  

for idx in range(len(pieces)):
  p = pieces[idx]
  if idx != 0 and p == pieces[idx - 1]: # extend prev result again
    all_r_cls.extend(rfreq_cls)
    all_p_cls.extend(polyph_cls)
    continue
  p = p + '.pkl'
  bar_pos, events = pickle_load(os.path.join(data_dir, p))
  events = events[ :bar_pos[-1] ]

  polyph_raw = np.reshape(
    compute_polyphonicity(events, n_bars=len(bar_pos)), (-1, 16)
  )
  rhythm_raw = np.reshape(
    get_onsets_timing(events, n_bars=len(bar_pos)), (-1, 16)
  )

  polyph_cls = np.searchsorted(polyphonicity_bounds, np.mean(polyph_raw, axis=-1)).tolist()
  rfreq_cls = np.searchsorted(rhym_intensity_bounds, np.mean(rhythm_raw, axis=-1)).tolist()

  pickle.dump(polyph_cls, open(os.path.join(
    polyph_out_dir, p), 'wb'
  ))
  pickle.dump(rfreq_cls, open(os.path.join(
    rhythm_out_dir, p), 'wb'
  ))

  all_r_cls.extend(rfreq_cls)
  all_p_cls.extend(polyph_cls)

print ('[rhythm classes]', Counter(all_r_cls))
print ('[polyph classes]', Counter(all_p_cls))

[rhythm classes] Counter({0: 2917246, 4: 2615224, 1: 2537060, 2: 2413000, 7: 2188198, 3: 2018130, 5: 2005684, 6: 1769110})
[polyph classes] Counter({0: 5395600, 2: 2086768, 6: 2081836, 1: 1977004, 3: 1824338, 4: 1772322, 5: 1759396, 7: 1566388})


In [41]:
'a953316683aaba87ed2671b7c5280cad_33.pkl' in os.listdir(polyph_out_dir)  # False

False

In [45]:
print(len(os.listdir("/content/remi_dataset/attr_cls/rhythm/")))

31986


In [ ]:
# read an example
with open("/content/remi_dataset/attr_cls/rhythm/ef41133867041cd16945edc7cda75077_1.pkl", "rb") as f:
  t2 = pickle.load(f)
print(t2)

[5, 4, 4, 0, 0]


In [ ]:
# with open("/content/remi_dataset/attr_cls/polyph/10.pkl", "rb") as f:
#   t3 = pickle.load(f)
# print(t3)

[0, 5, 5, 5, 4, 5, 5, 3, 4, 4, 4, 4, 4, 4, 4, 3, 4, 4, 5, 5, 3, 4, 4, 3, 4, 5, 4, 4, 3, 4, 4, 5, 4, 4, 5, 5, 3, 5, 5, 0, 0, 5, 5, 5, 4, 4, 5, 3, 4, 4, 4, 4, 4, 4, 4, 3, 4, 4, 5, 5, 3, 4, 4, 3, 4, 5, 4, 4, 3, 4, 4, 5, 4, 4, 5, 5, 3, 5, 5, 3, 4, 5, 4, 4, 4, 2, 0, 0]


In [42]:
!mv /content/content/remi_dataset /content/

In [ ]:
# tar intermediate results to Gdrive
!tar -czvf "/content/drive/MyDrive/Capstone/dataset/remi_dataset_0926_updated.tar.gz" "/content/remi_dataset"

In [ ]:
# # untar intermediate results to local
# !tar -xzvf "/content/drive/MyDrive/Capstone/dataset/remi_dataset_0907_updated.tar.gz" -C "./"

In [ ]:
len(chunk_id_list)

34241

In [ ]:
concatenated = []
for i in range(len(remi_data)):
  bar_pos, events = remi_data[i]
  # read rhythm scores
  with open("/content/remi_dataset/attr_cls/rhythm/{}.pkl".format(chunk_id_list[i]), "rb") as f:
    rhythm_scores = pickle.load(f)
  # read polyph scores
  with open("/content/remi_dataset/attr_cls/polyph/{}.pkl".format(chunk_id_list[i]), "rb") as f:
    polyph_scores = pickle.load(f)
  concatenated.append((bar_pos, events, rhythm_scores, polyph_scores))

In [ ]:
for i in concatenated[5]:
  print(i)

[0, 35, 68, 101, 134, 167, 200, 234, 268, 301, 334, 367, 400, 442, 488, 534]
[{'name': 'Bar', 'value': None}, {'name': 'Beat', 'value': 0}, {'name': 'Chord', 'value': 'N_N'}, {'name': 'Tempo', 'value': 119}, {'name': 'Note_Pitch', 'value': 47}, {'name': 'Note_Velocity', 'value': 102}, {'name': 'Note_Duration', 'value': 120}, {'name': 'Beat', 'value': 2}, {'name': 'Note_Pitch', 'value': 47}, {'name': 'Note_Velocity', 'value': 88}, {'name': 'Note_Duration', 'value': 120}, {'name': 'Beat', 'value': 4}, {'name': 'Note_Pitch', 'value': 47}, {'name': 'Note_Velocity', 'value': 96}, {'name': 'Note_Duration', 'value': 120}, {'name': 'Beat', 'value': 6}, {'name': 'Note_Pitch', 'value': 47}, {'name': 'Note_Velocity', 'value': 90}, {'name': 'Note_Duration', 'value': 120}, {'name': 'Beat', 'value': 8}, {'name': 'Note_Pitch', 'value': 47}, {'name': 'Note_Velocity', 'value': 96}, {'name': 'Note_Duration', 'value': 120}, {'name': 'Beat', 'value': 10}, {'name': 'Note_Pitch', 'value': 47}, {'name': 'Not

In [ ]:
# get recording->track mapping
FILES = []
rec_tra_map = {}
for i in filelist:
  filename = i.rstrip('\n')
  loc_lpd = "lpd_5/lpd_5_matched/"
  loc_lmd = "lmd_matched/"
  loc = "{}/{}/{}/{}/".format(filename[2], filename[3], filename[4], filename)
  for i in os.listdir(loc_lpd + loc):
    rec = i.rstrip('.npz')
    rec_tra_map[rec] = filename
    FILES.append(loc_lmd + loc + rec + '.mid')
len(FILES)

10913

In [ ]:
# rec_tra_map
!mkdir final_data_0907

In [ ]:
for i in range(len(concatenated)):
  chunk_id = chunk_id_list[i]
  rec_id = chunk_id.split("_")[0]
  track_id = rec_tra_map[rec_id]
  fn = f"{track_id}_{chunk_id}"
  np.savez("/content/final_data_0907/{}.npz".format(fn), np.array(concatenated[i]))

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  


In [ ]:
len(os.listdir("/content/final_data_0907"))

34241

In [ ]:
# tar intermediate results to Gdrive
!tar -czvf "/content/drive/MyDrive/Capstone/dataset/final_data_0907.tar.gz" "/content/final_data_0907"

Streaming output truncated to the last 5000 lines.
/content/final_data_0907/TRBROST128F148C641_d3e8fec3e0330e200f32d7be54ccbdb7_4.npz
/content/final_data_0907/TRZHBZC12903CA2ED7_f18faf70abf253aa1e528e715a56d091_2.npz
/content/final_data_0907/TRYTDVM128F4298393_7790cd2829ba4a0a1557011cadf40789_0.npz
/content/final_data_0907/TRWLKLI128F42307B4_d3e437761d57ab1a2f78ac6881aefab5_0.npz
/content/final_data_0907/TRUYXFE128F4260280_aea65221e74a16e9191b91e29f687075_1.npz
/content/final_data_0907/TRVPRRU12903CCFC74_75d278b9c35219f59e25373adfc231af_4.npz
/content/final_data_0907/TRGJGBQ128F4237AAC_35884ff408e240de6176e2ba9829c5fd_0.npz
/content/final_data_0907/TRWYDZN128F4294E51_8f45f8e4b54ba960c22ea1fbfd375691_16.npz
/content/final_data_0907/TRUVFAR128F92CA52B_fe8406ead56000a48f41191dd7753ed9_2.npz
/content/final_data_0907/TRKKQGM128F93351C3_bc9f3e43358f55213e65b97e405d1955_0.npz
/content/final_data_0907/TRVCJZG128E0791710_366d60d282adad7c862ca206da17bf32_0.npz
/content/final_data_0907/TROTIYV128

In [ ]:
# # untar intermediate results to local
# !tar -xzvf "/content/drive/MyDrive/Capstone/dataset/final_data_0907.tar.gz" -C "./"

# ends here

In [ ]:
# # dataset provided by compound... 
# !unzip /content/dataset.zip

In [ ]:

# with open("/content/4.pkl", "rb") as f:
#   tt2 = pickle.load(f)
# print(tt2)

[{'tempo': 0, 'chord': 0, 'bar-beat': 'Bar', 'type': 'Metrical', 'pitch': 0, 'duration': 0, 'velocity': 0}, {'tempo': 'Tempo_110', 'chord': 'G#_m7', 'bar-beat': 'Beat_0', 'type': 'Metrical', 'pitch': 0, 'duration': 0, 'velocity': 0}, {'tempo': 0, 'chord': 0, 'bar-beat': 0, 'type': 'Note', 'pitch': 'Note_Pitch_66', 'duration': 'Note_Duration_960', 'velocity': 'Note_Velocity_48'}, {'tempo': 0, 'chord': 0, 'bar-beat': 0, 'type': 'Note', 'pitch': 'Note_Pitch_63', 'duration': 'Note_Duration_960', 'velocity': 'Note_Velocity_40'}, {'tempo': 0, 'chord': 0, 'bar-beat': 0, 'type': 'Note', 'pitch': 'Note_Pitch_56', 'duration': 'Note_Duration_960', 'velocity': 'Note_Velocity_40'}, {'tempo': 0, 'chord': 0, 'bar-beat': 0, 'type': 'Note', 'pitch': 'Note_Pitch_40', 'duration': 'Note_Duration_0', 'velocity': 'Note_Velocity_40'}, {'tempo': 0, 'chord': 0, 'bar-beat': 0, 'type': 'Note', 'pitch': 'Note_Pitch_59', 'duration': 'Note_Duration_960', 'velocity': 'Note_Velocity_40'}, {'tempo': 'Tempo_119', 'chor

In [ ]:
# tt2

In [ ]:
# np.load("/content/0.npy")

array([  0,   1, 149, ..., 161,   0, 150])

In [ ]:
print(os.listdir("/content/final_data"))

['TRCAUAJ128F9316B07.npz', 'TRRWTCT128F14906B9.npz', 'TRHBFEF128F4286196.npz', 'TRWMHRC128F931F4C8.npz', 'TRAIYAV12903CE8475.npz', 'TRPKRBI128EF350B84.npz', 'TRBVXJK128F4262FA2.npz', 'TRUTUSD128F92EF9C5.npz', 'TRIAPYI128F42A3632.npz', 'TRWXJJQ128F427008B.npz', 'TRFNSIF128E078F147.npz', 'TRPYZRF128F4271A39.npz', 'TRPYQGC128F4262982.npz', 'TRFWJHA128EF3425DB.npz', 'TRZMGET128F9305E8E.npz', 'TRHZHBP128F425A1AF.npz', 'TRRVJXU128F428D205.npz', 'TRJCYLI12903CCC65C.npz', 'TRKJBHI128F427A724.npz', 'TRHSWLN128F92E8F48.npz', 'TRQGPOF128F930FF62.npz', 'TRXIDNF128F92F2C26.npz', 'TRHGRCL128F92E182D.npz', 'TREWFGS128F93075E5.npz', 'TRNBZCT128F4242788.npz', 'TRMWCEE128F426D0AE.npz', 'TRQUMTI128F425DB89.npz', 'TRVRTCQ128F4293569.npz', 'TRMLRJN12903CAC997.npz', 'TRFXGHQ128F9349BD3.npz', 'TRZEJSA128F92DE1B3.npz', 'TRUGJMC12903CF7C3B.npz', 'TRPICIB128F4267519.npz', 'TRTBZQV128F4270293.npz', 'TRZXWPS128F424E5C5.npz', 'TRIHKSB128F427A327.npz', 'TRZWYXR128F427195C.npz', 'TRBISBN128F4267AB6.npz', 'TRYHWKI128

In [ ]:
with np.load('/content/final_data/TRCAUAJ128F9316B07.npz', allow_pickle=True) as data:
    a = data['arr_0']

In [ ]:
a

array([list([0, 217, 471, 609, 802, 1270, 1673, 1905, 2133, 2379, 2616, 2831, 3114, 3277]),
       list([{'name': 'Bar', 'value': None}, {'name': 'Beat', 'value': 0}, {'name': 'Chord', 'value': 'N_N'}, {'name': 'Tempo', 'value': 77}, {'name': 'Beat', 'value': 3}, {'name': 'Note_Pitch', 'value': 37}, {'name': 'Note_Velocity', 'value': 80}, {'name': 'Note_Duration', 'value': 0}, {'name': 'Beat', 'value': 5}, {'name': 'Note_Pitch', 'value': 37}, {'name': 'Note_Velocity', 'value': 80}, {'name': 'Note_Duration', 'value': 0}, {'name': 'Beat', 'value': 6}, {'name': 'Note_Pitch', 'value': 37}, {'name': 'Note_Velocity', 'value': 80}, {'name': 'Note_Duration', 'value': 0}, {'name': 'Beat', 'value': 7}, {'name': 'Note_Pitch', 'value': 37}, {'name': 'Note_Velocity', 'value': 80}, {'name': 'Note_Duration', 'value': 0}, {'name': 'Beat', 'value': 8}, {'name': 'Note_Pitch', 'value': 37}, {'name': 'Note_Velocity', 'value': 80}, {'name': 'Note_Duration', 'value': 0}, {'name': 'Beat', 'value': 9}, {'name

In [ ]:
!tar -czvf final_data0412.tar.gz /content/final_data/

tar: Removing leading `/' from member names
/content/final_data/
/content/final_data/TRCAUAJ128F9316B07.npz
/content/final_data/TRRWTCT128F14906B9.npz
/content/final_data/TRHBFEF128F4286196.npz
/content/final_data/TRWMHRC128F931F4C8.npz
/content/final_data/TRAIYAV12903CE8475.npz
/content/final_data/TRPKRBI128EF350B84.npz
/content/final_data/TRBVXJK128F4262FA2.npz
/content/final_data/TRUTUSD128F92EF9C5.npz
/content/final_data/TRIAPYI128F42A3632.npz
/content/final_data/TRWXJJQ128F427008B.npz
/content/final_data/TRFNSIF128E078F147.npz
/content/final_data/TRPYZRF128F4271A39.npz
/content/final_data/TRPYQGC128F4262982.npz
/content/final_data/TRFWJHA128EF3425DB.npz
/content/final_data/TRZMGET128F9305E8E.npz
/content/final_data/TRHZHBP128F425A1AF.npz
/content/final_data/TRRVJXU128F428D205.npz
/content/final_data/TRJCYLI12903CCC65C.npz
/content/final_data/TRKJBHI128F427A724.npz
/content/final_data/TRHSWLN128F92E8F48.npz
/content/final_data/TRQGPOF128F930FF62.npz
/content/final_data/TRXIDNF128F9

In [ ]:
###
!tar -xzvf /content/lmd_matched.tar.gz